# <div align = "Center" style="color: rgb(0, 255, 0);"> New Model Dashboard </div>

# Define Library

In [1]:
# %% [markdown]
# # Jupyter Notebook Loading Header
#
# This is a custom loading header for Jupyter Notebooks in Visual Studio Code.
# It includes common imports and settings to get you started quickly.
# %% [markdown]
## Import Libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from google.cloud import bigquery
from google.cloud import storage
import os
import tempfile
import time
from datetime import datetime
import uuid
import joblib
import uuid

import gcsfs
import duckdb as dd
import pickle
import joblib
from typing import Union
import io

path = r'C:\Users\Dwaipayan\AppData\Roaming\gcloud\legacy_credentials\dchakroborti@tonikbank.com\adc.json'
os.environ['GOOGLE_APPLICATION_CREDENTIALS'] = path
client = bigquery.Client(project='prj-prod-dataplatform')
os.environ["GOOGLE_CLOUD_PROJECT"] = "prj-prod-dataplatform"
# %% [markdown]
## Configure Settings
# Set options or configurations as needed
pd.set_option('display.max_columns', None)
pd.set_option("Display.max_rows", 100)


`Create the merged Transformed table`

# Merged final table

In [2]:
schema3 = 'dap_ds_poweruser_playground'
tab1 = 'temp_final_model_transformed_data'

In [3]:
sq = f"""
create or replace table {schema3}.{tab1} as
SELECT cast(customerId as numeric)customerId, digitalLoanAccountId, cast(prediction as string)prediction, start_time, end_time  
, modelDisplayName
, modelVersionId
, calcFeature
, 'ml_model_run_details' source
FROM `prj-prod-dataplatform.audit_balance.ml_model_run_details` 
qualify row_number() over(partition by customerId ,digitalLoanAccountId, modelDisplayName order by start_time
desc) = 1

union all 

select customerId, digitalLoanAccountId, cast(prediction as string)prediction, datetime(start_time)start_time, datetime(end_time) end_time 
, modelDisplayName
, modelVersionId
, calcFeature 
, 'Manual_Backscore_tables' source
from dap_ds_poweruser_playground.temp_model_transformed_data
;
"""
job = client.query(sq)
job.result()  # Wait for the job to complete.
time.sleep(5) # Delays for 30 seconds
print(f'Table {schema3}.{tab1} created successfully')



Table dap_ds_poweruser_playground.temp_final_model_transformed_data created successfully


In [4]:
sq = f"""select * from {schema3}.{tab1};"""
df = client.query(sq).to_dataframe(progress_bar_type='tqdm')

Job ID 0aa42204-c5b0-4d6b-80a0-b5663703e092 successfully executed: 100%|██████████|

C:\Users\Dwaipayan\AppData\Roaming\Python\Python312\site-packages\google\cloud\bigquery\table.py:1900: UserWarning: BigQuery Storage module not found, fetch data with the REST endpoint instead.
  warnings.warn(



Downloading: 100%|██████████|


In [5]:
print(f"The shape of the dataframe is:\t {schema3}.{tab1}")

The shape of the dataframe is:	 dap_ds_poweruser_playground.temp_final_model_transformed_data


In [6]:
modelmetadata = 'model_metadata'

sq = f"""create or replace table {schema3}.{modelmetadata} as
select 
'Beta - AppsScoreModel' as modelDisplayName, 
'ln_appln_submit_datetime' datefield, 
date('2023-07-01') train_sdate, 
date('2024-06-30') train_edate, 
date('2024-07-01') test_sdate, 
date(current_date()) test_edate,
date('2023-04-01') datereadstartdate
union all 
select 
'Beta - DemoScoreModel' as modelDisplayName, 
'ln_appln_submit_datetime' datefield, 
date('2023-07-01') train_sdate, 
date('2024-06-30') train_edate, 
date('2024-07-01') test_sdate, 
date(current_date()) test_edate,
date('2023-04-01') datereadstartdate
union all 
select 
'Alpha - CIC-SIL-Model' as modelDisplayName, 
'ln_appln_submit_datetime' datefield, 
date('2023-07-01') train_sdate, 
date('2024-06-30') train_edate, 
date('2024-07-01') test_sdate, 
date(current_date()) test_edate,
date('2023-04-01') datereadstartdate
union all 
Select 
'Beta - StackScoreModel' as modelDisplayName,
'ln_appln_submit_datetime' datefield, 
date('2023-07-01') train_sdate, 
date('2024-06-30') train_edate, 
date('2024-07-01') test_sdate, 
date(current_date()) test_edate,
date('2023-04-01') datereadstartdate
union all 
select 
'Alpha - StackingModel' modelDisplayName,
'ln_appln_submit_datetime' datefield, 
date('2023-07-01') train_sdate, 
date('2024-06-30') train_edate, 
date('2024-07-01') test_sdate, 
date(current_date()) test_edate,
date('2023-04-01') datereadstartdate
-- union all 
-- credo_quick_score
-- credo_sil_score
-- credo_flex_score
-- credo_flex_score
-- credo_gen_score
"""
job = client.query(sq)
job.result()  # Wait for the job to complete.
time.sleep(5) # Delays for 30 seconds
print(f'Table {schema3}.{modelmetadata} created successfully')


Table dap_ds_poweruser_playground.model_metadata created successfully


In [7]:
schema3 = 'dap_ds_poweruser_playground'
finalmodeltransformeddate = 'final_model_transformed_data'

sq = f"""create or replace table {schema3}.{finalmodeltransformeddate} as 
select t1.*, 
m1.datefield,
m1.train_sdate,
m1.train_edate,
m1.test_sdate,
m1.test_edate,
m1.datereadstartdate
from {schema3}.{tab1} as t1
left join {schema3}.{modelmetadata} m1 on m1.modelDisplayName = t1.modelDisplayName
"""

job = client.query(sq)
job.result()  # Wait for the job to complete.
time.sleep(5) # Delays for 30 seconds
print(f'Table {schema3}.{finalmodeltransformeddate} created successfully')

Table dap_ds_poweruser_playground.final_model_transformed_data created successfully


In [8]:
sq = """select * from dap_ds_poweruser_playground.final_model_transformed_data;"""

df = client.query(sq).to_dataframe(progress_bar_type = 'tqdm')

df.head()

Job ID dca47684-e4bc-4253-a224-2772727a3b08 successfully executed: 100%|██████████|
Downloading: 100%|██████████|


customerId                  digitalLoanAccountId  \
0  3533512.000000000  84c18358-87ca-4779-9867-c45133c596da   
1  3612171.000000000  476c6981-9154-4c01-8e2f-ffc5a080505f   
2  3646368.000000000  cf9ec85f-7f6d-4376-8a7e-013687344742   
3  3604711.000000000  bbcb5079-5a98-43cb-aa76-6d93939cf0fc   
4  3560676.000000000  759203c6-cb87-465f-af34-5fd3963a6524   

                                          prediction  \
0  {'cb_score': 0.45104540768218293, 'dl_score': ...   
1                                        0.065411098   
2                                       0.1230553577   
3                                       0.0658951515   
4                                       0.0675954096   

                  start_time                   end_time  \
0 2025-07-02 04:55:25.456504 2025-07-02 04:55:25.907049   
1 2025-08-10 08:23:02.960325 2025-08-10 08:23:03.023408   
2 2025-08-27 07:10:56.404938 2025-08-27 07:10:56.471600   
3 2025-08-07 03:06:09.038394 2025-08-07 03:06:09.106790   
4 2025-07-16 08:57:03.087471 2025-07-16 08:57:03.151861   

        modelDisplayName modelVersionId  \
0  Beta - AppsScoreModel             v1   
1  Beta - DemoScoreModel             v1   
2  Beta - DemoScoreModel             v1   
3  Beta - DemoScoreModel             v1   
4  Beta - DemoScoreModel             v1   

                                         calcFeature                source  \
0  {"app_cnt_rated_for_3plus_ever":20,"app_cnt_ed...  ml_model_run_details   
1  {"beta_de_ln_vas_opted_flag": "1", "beta_de_ln...  ml_model_run_details   
2  {"beta_de_ln_vas_opted_flag": "0", "beta_de_ln...  ml_model_run_details   
3  {"beta_de_ln_vas_opted_flag": "0", "beta_de_ln...  ml_model_run_details   
4  {"beta_de_ln_vas_opted_flag": "1", "beta_de_ln...  ml_model_run_details   

                  datefield train_sdate train_edate  test_sdate  test_edate  \
0  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   
1  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   
2  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   
3  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   
4  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   

  datereadstartdate  
0        2023-04-01  
1        2023-04-01  
2        2023-04-01  
3        2023-04-01  
4        2023-04-01

In [9]:
df.head(100).to_csv(r"D:\OneDrive - Tonik Financial Pte Ltd\MyStuff\Data Engineering\Model_Monitoring\New_Model_Monitoring\Data\sample.csv", index = False)

In [22]:
import pandas as pd
import ast
import json
from io import StringIO

def safe_literal_eval(s):
    """Safely evaluate string representation of dict/list"""
    if pd.isna(s) or s == '':
        return {}
    try:
        # Try parsing as Python literal first
        return ast.literal_eval(s)
    except:
        try:
            # Try parsing as JSON
            return json.loads(s.replace("'", '"'))
        except:
            # If all fails, return empty dict
            return {}

def flatten_calc_features(df):
    """Flatten the calcFeature column into separate columns"""
    # Create a copy to avoid modifying original
    result_df = df.copy()
    
    # List to store all feature names we encounter
    all_features = set()
    
    # Dictionary to store flattened features for each row
    flattened_features = []
    
    for idx, row in df.iterrows():
        calc_feature_str = row['calcFeature']
        flattened_row = {}
        
        if pd.notna(calc_feature_str):
            # Parse the calcFeature string
            features_dict = safe_literal_eval(calc_feature_str)
            
            # Flatten the dictionary
            if isinstance(features_dict, dict):
                for key, value in features_dict.items():
                    # Clean the key name (remove quotes, etc.)
                    clean_key = str(key).replace('"', '').replace("'", '').strip()
                    flattened_row[clean_key] = value
                    all_features.add(clean_key)
        
        flattened_features.append(flattened_row)
    
    # Create DataFrame from flattened features
    features_df = pd.DataFrame(flattened_features)
    
    # Ensure all columns are present (fill missing with NaN)
    for feature in all_features:
        if feature not in features_df.columns:
            features_df[feature] = None
    
    # Reorder columns alphabetically for consistency
    features_df = features_df.reindex(sorted(features_df.columns), axis=1)
    
    # Reset index to ensure proper alignment
    features_df.reset_index(drop=True, inplace=True)
    result_df.reset_index(drop=True, inplace=True)
    
    # Concatenate with original DataFrame (without calcFeature column)
    final_df = pd.concat([result_df.drop('calcFeature', axis=1), features_df], axis=1)
    
    return final_df

def clean_column_names(df):
    """Clean column names by removing special characters"""
    df.columns = [col.replace('"', '').replace("'", '').strip() for col in df.columns]
    return df



In [23]:
df.columns

Index(['customerId', 'digitalLoanAccountId', 'prediction', 'start_time',
       'end_time', 'modelDisplayName', 'modelVersionId', 'calcFeature',
       'source', 'datefield', 'train_sdate', 'train_edate', 'test_sdate',
       'test_edate', 'datereadstartdate'],
      dtype='object')

In [24]:
# Flatten the data
flattened_df = flatten_calc_features(df)

# Clean column names
flattened_df = clean_column_names(flattened_df)

# Display information about the flattened DataFrame
print(f"Original shape: {df.shape}")
print(f"Flattened shape: {flattened_df.shape}")
print(f"\nOriginal columns: {len(df.columns)}")
print(f"Flattened columns: {len(flattened_df.columns)}")

# Show the new feature columns that were created
calc_feature_columns = [col for col in flattened_df.columns if col not in df.columns and col != 'calcFeature']
print(f"\nNew feature columns created: {len(calc_feature_columns)}")
print("Feature columns:", sorted(calc_feature_columns))

# Display first few rows to verify
print("\nFirst 3 rows of flattened data:")
# print(flattened_df.head(3))

# Save to new CSV if needed
# flattened_df.to_csv('flattened_sample.csv', index=False)

<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: invalid escape sequence '\/'
<unknown>:1: SyntaxWarning: inv

Original shape: (2284981, 15)
Flattened shape: (2284981, 208)

Original columns: 15
Flattened columns: 208

New feature columns created: 194
Feature columns: ['app_avg_time_bw_installed_mins_30d', 'app_cnt_absence_tag_30d', 'app_cnt_absence_tag_90d', 'app_cnt_business_ever', 'app_cnt_competitors_30d', 'app_cnt_competitors_90d', 'app_cnt_education_ever', 'app_cnt_finance_30d', 'app_cnt_finance_7d', 'app_cnt_finance_90d', 'app_cnt_music_and_audio_ever', 'app_cnt_payday_90d', 'app_cnt_rated_for_3plus_ever', 'app_cnt_travel_and_local_ever', 'app_first_competitors_install_to_apply_days', 'app_first_payday_install_to_apply_days', 'app_median_time_bw_installed_mins_30d', 'app_vel_finance_30_over_365', 'apps_score', 'beta_de_ln_age_bin', 'beta_de_ln_appln_day_of_week', 'beta_de_ln_brand_bin', 'beta_de_ln_doc_type_rolled', 'beta_de_ln_education_level', 'beta_de_ln_email_primary_domain', 'beta_de_ln_employment_type_new_bin', 'beta_de_ln_industry_new_bin', 'beta_de_ln_marital_status', 'beta_de_ln

In [25]:
flattened_df['customerId'] = flattened_df['customerId'].astype(str).str.replace('.000000000', '', regex=False)
flattened_df.head()

customerId                  digitalLoanAccountId  \
0    3533512  84c18358-87ca-4779-9867-c45133c596da   
1    3612171  476c6981-9154-4c01-8e2f-ffc5a080505f   
2    3646368  cf9ec85f-7f6d-4376-8a7e-013687344742   
3    3604711  bbcb5079-5a98-43cb-aa76-6d93939cf0fc   
4    3560676  759203c6-cb87-465f-af34-5fd3963a6524   

                                          prediction  \
0  {'cb_score': 0.45104540768218293, 'dl_score': ...   
1                                        0.065411098   
2                                       0.1230553577   
3                                       0.0658951515   
4                                       0.0675954096   

                  start_time                   end_time  \
0 2025-07-02 04:55:25.456504 2025-07-02 04:55:25.907049   
1 2025-08-10 08:23:02.960325 2025-08-10 08:23:03.023408   
2 2025-08-27 07:10:56.404938 2025-08-27 07:10:56.471600   
3 2025-08-07 03:06:09.038394 2025-08-07 03:06:09.106790   
4 2025-07-16 08:57:03.087471 2025-07-16 08:57:03.151861   

        modelDisplayName modelVersionId                source  \
0  Beta - AppsScoreModel             v1  ml_model_run_details   
1  Beta - DemoScoreModel             v1  ml_model_run_details   
2  Beta - DemoScoreModel             v1  ml_model_run_details   
3  Beta - DemoScoreModel             v1  ml_model_run_details   
4  Beta - DemoScoreModel             v1  ml_model_run_details   

                  datefield train_sdate train_edate  test_sdate  test_edate  \
0  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   
1  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   
2  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   
3  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   
4  ln_appln_submit_datetime  2023-07-01  2024-06-30  2024-07-01  2025-09-23   

  datereadstartdate  app_avg_time_bw_installed_mins_30d  \
0        2023-04-01                           3234.9125   
1        2023-04-01                                 NaN   
2        2023-04-01                                 NaN   
3        2023-04-01                                 NaN   
4        2023-04-01                                 NaN   

   app_cnt_absence_tag_30d  app_cnt_absence_tag_90d  app_cnt_business_ever  \
0                      0.0                      0.0                    1.0   
1                      NaN                      NaN                    NaN   
2                      NaN                      NaN                    NaN   
3                      NaN                      NaN                    NaN   
4                      NaN                      NaN                    NaN   

   app_cnt_competitors_30d  app_cnt_competitors_90d  app_cnt_education_ever  \
0                      0.0                      0.0                     0.0   
1                      NaN                      NaN                     NaN   
2                      NaN                      NaN                     NaN   
3                      NaN                      NaN                     NaN   
4                      NaN                      NaN                     NaN   

   app_cnt_finance_30d  app_cnt_finance_7d  app_cnt_finance_90d  \
0                  0.0                 0.0                  0.0   
1                  NaN                 NaN                  NaN   
2                  NaN                 NaN                  NaN   
3                  NaN                 NaN                  NaN   
4                  NaN                 NaN                  NaN   

   app_cnt_music_and_audio_ever  app_cnt_payday_90d  \
0                           0.0                 0.0   
1                           NaN                 NaN   
2                           NaN                 NaN   
3                           NaN                 NaN   
4                           NaN                 NaN   

   app_cnt_rated_for_3plus_ever  app_cnt_travel_and_local_ever  \
0                   

In [26]:
flattened_df.to_csv(r"D:\OneDrive - Tonik Financial Pte Ltd\MyStuff\Data Engineering\Model_Monitoring\New_Model_Monitoring\Data\flattened_df.csv", index = False)

In [ ]:
import pandas as pd
import numpy as pd

def calculate_psi_for_model(model_df, model_name):
    """
    Calculate PSI for a specific model's data
    """
    # Convert prediction to numeric if it's not already
    model_df['prediction'] = pd.to_numeric(model_df['prediction'], errors='coerce')
    
    # Convert datefield to datetime if it's not already
    if model_df['datefield'].dtype != 'datetime64[ns]':
        model_df['datefield'] = pd.to_datetime(model_df['datefield'])
    
    # Get date ranges from the first row (assuming they're consistent for the model)
    train_sdate = model_df['train_sdate'].iloc[0]
    train_edate = model_df['train_edate'].iloc[0]
    test_sdate = model_df['test_sdate'].iloc[0]
    test_edate = model_df['test_edate'].iloc[0]
    
    # Convert date ranges to datetime
    train_sdate = pd.to_datetime(train_sdate)
    train_edate = pd.to_datetime(train_edate)
    test_sdate = pd.to_datetime(test_sdate)
    test_edate = pd.to_datetime(test_edate)
    
    # Separate train and test data based on datefield
    train_df = model_df[(model_df['datefield'] >= train_sdate) & (model_df['datefield'] <= train_edate)]
    test_df = model_df[(model_df['datefield'] >= test_sdate) & (model_df['datefield'] <= test_edate)]
    
    # Check if we have sufficient data
    if len(train_df) == 0 or len(test_df) == 0:
        print(f"Warning: Insufficient data for model {model_name}")
        return pd.DataFrame()
    
    # Calculate decile bins for the entire training set
    train_deciles = pd.qcut(train_df['prediction'], 10, labels=False, retbins=True)
    train_decile_bins = train_deciles[1]
    
    # Function to calculate PSI using the pre-defined decile bins
    def calculate_psi_with_bins(data_scores, decile_bins):
        """Calculates PSI using pre-defined decile bins."""
        data_deciles = pd.cut(data_scores, bins=decile_bins, labels=False, include_lowest=True)
        distribution = pd.Series(data_deciles).value_counts().sort_index() / len(data_scores)
        
        # Align with training distribution
        all_bins = range(10)  # Assuming 10 deciles
        distribution_aligned = distribution.reindex(all_bins, fill_value=0)
        train_dist_aligned = pd.Series(train_deciles[0]).value_counts().sort_index() / len(train_df['prediction'])
        train_dist_aligned = train_dist_aligned.reindex(all_bins, fill_value=0)
        
        # Replace zeros with small value to avoid division by zero in log
        distribution_aligned = distribution_aligned.replace(0, 1e-10)
        train_dist_aligned = train_dist_aligned.replace(0, 1e-10)
        
        psi_values = (distribution_aligned - train_dist_aligned) * np.log(distribution_aligned / train_dist_aligned)
        return psi_values.sum()
    
    # Calculate PSI for the entire training set
    train_psi = calculate_psi_with_bins(train_df['prediction'], train_decile_bins)
    
    # Get the last month of the training set
    last_train_month = train_df['datefield'].max()
    last_train_month_str = last_train_month.strftime('%Y-%m')
    
    # Calculate monthly PSI for the test set
    monthly_psi_results = []
    
    # Add the train set PSI to the results (with the correct last month)
    monthly_psi_results.append({
        'modelDisplayName': model_name,
        'Month': last_train_month_str,
        'scorename': 'prediction',
        'DateCategory': 'Training',
        'psivalues': train_psi,
        'account_count': train_df['digitalLoanAccountId'].nunique(),
        'train_sdate': train_sdate.strftime('%Y-%m-%d'),
        'train_edate': train_edate.strftime('%Y-%m-%d'),
        'test_sdate': test_sdate.strftime('%Y-%m-%d'),
        'test_edate': test_edate.strftime('%Y-%m-%d')
    })
    
    # Calculate monthly PSI for the test set
    # Extract year-month from datefield for monthly grouping
    test_df = test_df.copy()
    test_df['year_month'] = test_df['datefield'].dt.to_period('M')
    
    for month_period in sorted(test_df['year_month'].unique()):
        month_df = test_df[test_df['year_month'] == month_period]
        if not month_df.empty and len(month_df) > 0:
            month_psi = calculate_psi_with_bins(month_df['prediction'], train_decile_bins)
            monthly_psi_results.append({
                'modelDisplayName': model_name,
                'Month': month_period.strftime('%Y-%m'),
                'scorename': 'prediction',
                'DateCategory': 'Monthly',
                'psivalues': month_psi,
                'account_count': month_df['digitalLoanAccountId'].nunique(),
                'train_sdate': train_sdate.strftime('%Y-%m-%d'),
                'train_edate': train_edate.strftime('%Y-%m-%d'),
                'test_sdate': test_sdate.strftime('%Y-%m-%d'),
                'test_edate': test_edate.strftime('%Y-%m-%d')
            })
    
    return pd.DataFrame(monthly_psi_results)

# Main code to loop through all models and create combined output
def calculate_psi_for_all_models(df):
    """
    Calculate PSI for all models in the dataframe
    """
    # Get unique model names
    unique_models = df['modelDisplayName'].unique()
    
    # Initialize list to store results for all models
    all_models_results = []
    
    # Loop through each model
    for model_name in unique_models:
        print(f"Processing model: {model_name}")
        
        # Filter data for current model
        model_df = df[df['modelDisplayName'] == model_name].copy()
        
        # Calculate PSI for this model
        model_results = calculate_psi_for_model(model_df, model_name)
        
        # Append to results list if not empty
        if not model_results.empty:
            all_models_results.append(model_results)
    
    # Combine all results into a single dataframe
    if all_models_results:
        final_output_df = pd.concat(all_models_results, ignore_index=True)
        # Rename psivalues column to be more descriptive
        final_output_df.rename(columns={'psivalues': 'prediction_psivalues'}, inplace=True)
        return final_output_df
    else:
        return pd.DataFrame()

# Usage example:
# Assuming your dataframe is called 'df'
# final_result = calculate_psi_for_all_models(df)
# final_result

# Alternative version if you want to process one model at a time and see progress:
def calculate_psi_for_all_models_with_progress(df):
    """
    Calculate PSI for all models with detailed progress reporting
    """
    unique_models = df['modelDisplayName'].unique()
    all_models_results = []
    
    print(f"Found {len(unique_models)} models to process")
    
    for i, model_name in enumerate(unique_models, 1):
        print(f"Processing model {i}/{len(unique_models)}: {model_name}")
        
        model_df = df[df['modelDisplayName'] == model_name].copy()
        
        # Check if date ranges are consistent within the model
        unique_train_dates = model_df[['train_sdate', 'train_edate', 'test_sdate', 'test_edate']].drop_duplicates()
        if len(unique_train_dates) > 1:
            print(f"Warning: Model {model_name} has inconsistent date ranges. Using first row values.")
        
        model_results = calculate_psi_for_model(model_df, model_name)
        
        if not model_results.empty:
            all_models_results.append(model_results)
            print(f"  Completed: {len(model_results)} records generated")
        else:
            print(f"  Warning: No results generated for model {model_name}")
    
    if all_models_results:
        final_output_df = pd.concat(all_models_results, ignore_index=True)
        final_output_df.rename(columns={'psivalues': 'prediction_psivalues'}, inplace=True)
        
        print(f"\nProcessing complete!")
        print(f"Total records generated: {len(final_output_df)}")
        print(f"Models processed: {len(unique_models)}")
        
        return final_output_df
    else:
        print("No results generated for any models")
        return pd.DataFrame()
# Use this function for better progress tracking
# final_result = calculate_psi_for_all_models_with_progress(df)


In [28]:
# Usage example:
# Assuming your dataframe is called 'df'
final_result = calculate_psi_for_all_models(flattened_df)
final_result

Processing model: Beta - AppsScoreModel


AttributeError: module 'numpy' has no attribute 'to_numeric'

In [38]:
import pandas as pd
import numpy as np

def calculate_psi_for_model(model_df, model_name):
    """
    Calculate PSI for a specific model's data with better date handling
    """
    try:
        # Create a copy to avoid modifying the original
        model_df = model_df.copy()
        
        # Convert prediction to numeric if it's not already
        model_df['prediction'] = pd.to_numeric(model_df['prediction'], errors='coerce')
        
        # Drop NaN values in prediction
        model_df = model_df.dropna(subset=['prediction'])
        
        # Check if datefield contains actual dates or column names
        print(f"Checking datefield for model {model_name}:")
        print(f"First few values: {model_df['datefield'].head().tolist()}")
        print(f"Data type: {model_df['datefield'].dtype}")
        
        # If datefield doesn't contain proper dates, try to find an actual date column
        date_column = None
        potential_date_columns = ['datefield', 'start_time', 'end_time', 'datereadstartdate']
        
        for col in potential_date_columns:
            if col in model_df.columns:
                try:
                    # Try to convert to datetime
                    test_date = pd.to_datetime(model_df[col].iloc[0], errors='coerce')
                    if not pd.isna(test_date):
                        date_column = col
                        print(f"Using {col} as date column")
                        break
                except:
                    continue
        
        if date_column is None:
            print(f"Warning: No valid date column found for model {model_name}")
            return pd.DataFrame()
        
        # Convert the selected date column to datetime
        model_df['date_used'] = pd.to_datetime(model_df[date_column], errors='coerce')
        
        # Drop rows where date conversion failed
        model_df = model_df.dropna(subset=['date_used'])
        
        if len(model_df) == 0:
            print(f"Warning: No valid dates found for model {model_name}")
            return pd.DataFrame()
        
        # Get date ranges from the first row
        train_sdate = model_df['train_sdate'].iloc[0]
        train_edate = model_df['train_edate'].iloc[0]
        test_sdate = model_df['test_sdate'].iloc[0]
        test_edate = model_df['test_edate'].iloc[0]
        
        # Convert date ranges to datetime
        try:
            train_sdate = pd.to_datetime(train_sdate)
            train_edate = pd.to_datetime(train_edate)
            test_sdate = pd.to_datetime(test_sdate)
            test_edate = pd.to_datetime(test_edate)
        except Exception as e:
            print(f"Error converting date ranges for model {model_name}: {e}")
            return pd.DataFrame()
        
        # Separate train and test data based on date_used
        train_df = model_df[(model_df['date_used'] >= train_sdate) & (model_df['date_used'] <= train_edate)]
        test_df = model_df[(model_df['date_used'] >= test_sdate) & (model_df['date_used'] <= test_edate)]
        
        # Check if we have sufficient data
        if len(train_df) < 10:  # Need at least 10 records for deciles
            print(f"Warning: Insufficient training data for model {model_name} ({len(train_df)} records)")
            return pd.DataFrame()
        
        if len(test_df) == 0:
            print(f"Warning: No test data for model {model_name}")
            return pd.DataFrame()
        
        # Calculate decile bins for the entire training set
        try:
            train_deciles = pd.qcut(train_df['prediction'], 10, labels=False, retbins=True, duplicates='drop')
            train_decile_bins = train_deciles[1]
        except Exception as e:
            print(f"Error calculating deciles for model {model_name}: {e}")
            return pd.DataFrame()
        
        # Function to calculate PSI using the pre-defined decile bins
        def calculate_psi_with_bins(data_scores, decile_bins):
            """Calculates PSI using pre-defined decile bins."""
            try:
                data_deciles = pd.cut(data_scores, bins=decile_bins, labels=False, include_lowest=True)
                distribution = pd.Series(data_deciles).value_counts().sort_index() / len(data_scores)
                
                # Align with training distribution
                all_bins = range(len(decile_bins)-1)  # Number of bins = len(bins)-1
                distribution_aligned = distribution.reindex(all_bins, fill_value=0)
                train_dist_aligned = pd.Series(train_deciles[0]).value_counts().sort_index() / len(train_df['prediction'])
                train_dist_aligned = train_dist_aligned.reindex(all_bins, fill_value=0)
                
                # Replace zeros with small value to avoid division by zero in log
                distribution_aligned = distribution_aligned.replace(0, 1e-10)
                train_dist_aligned = train_dist_aligned.replace(0, 1e-10)
                
                psi_values = (distribution_aligned - train_dist_aligned) * np.log(distribution_aligned / train_dist_aligned)
                return psi_values.sum()
            except Exception as e:
                print(f"Error calculating PSI: {e}")
                return float('nan')
        
        # Calculate PSI for the entire training set
        train_psi = calculate_psi_with_bins(train_df['prediction'], train_decile_bins)
        
        # Get the last month of the training set
        last_train_month = train_df['date_used'].max()
        last_train_month_str = last_train_month.strftime('%Y-%m')
        
        # Calculate monthly PSI for the test set
        monthly_psi_results = []
        
        # Add the train set PSI to the results
        monthly_psi_results.append({
            'modelDisplayName': model_name,
            'Month': last_train_month_str,
            'scorename': 'prediction',
            'DateCategory': 'Training',
            'psivalues': train_psi,
            'account_count': train_df['digitalLoanAccountId'].nunique(),
            'train_sdate': train_sdate.strftime('%Y-%m-%d'),
            'train_edate': train_edate.strftime('%Y-%m-%d'),
            'test_sdate': test_sdate.strftime('%Y-%m-%d'),
            'test_edate': test_edate.strftime('%Y-%m-%d'),
            'date_column_used': date_column
        })
        
        # Calculate monthly PSI for the test set
        test_df = test_df.copy()
        test_df['year_month'] = test_df['date_used'].dt.to_period('M')
        
        for month_period in sorted(test_df['year_month'].unique()):
            month_df = test_df[test_df['year_month'] == month_period]
            if not month_df.empty and len(month_df) > 0:
                month_psi = calculate_psi_with_bins(month_df['prediction'], train_decile_bins)
                monthly_psi_results.append({
                    'modelDisplayName': model_name,
                    'Month': month_period.strftime('%Y-%m'),
                    'scorename': 'prediction',
                    'DateCategory': 'Monthly',
                    'psivalues': month_psi,
                    'account_count': month_df['digitalLoanAccountId'].nunique(),
                    'train_sdate': train_sdate.strftime('%Y-%m-%d'),
                    'train_edate': train_edate.strftime('%Y-%m-%d'),
                    'test_sdate': test_sdate.strftime('%Y-%m-%d'),
                    'test_edate': test_edate.strftime('%Y-%m-%d'),
                    'date_column_used': date_column
                })
        
        return pd.DataFrame(monthly_psi_results)
    
    except Exception as e:
        print(f"Error processing model {model_name}: {e}")
        import traceback
        traceback.print_exc()
        return pd.DataFrame()

def calculate_psi_for_all_models(df):
    """
    Calculate PSI for all models in the dataframe
    """
    # Get unique model names
    unique_models = df['modelDisplayName'].unique()
    
    # Initialize list to store results for all models
    all_models_results = []
    
    print(f"Found {len(unique_models)} models to process")
    
    # Loop through each model
    for i, model_name in enumerate(unique_models, 1):
        print(f"\nProcessing model {i}/{len(unique_models)}: {model_name}")
        
        # Filter data for current model
        model_df = df[df['modelDisplayName'] == model_name].copy()
        
        # Calculate PSI for this model
        model_results = calculate_psi_for_model(model_df, model_name)
        
        # Append to results list if not empty
        if not model_results.empty:
            all_models_results.append(model_results)
            print(f"  Success: Generated {len(model_results)} records")
        else:
            print(f"  Warning: No results generated for model {model_name}")
    
    # Combine all results into a single dataframe
    if all_models_results:
        final_output_df = pd.concat(all_models_results, ignore_index=True)
        # Rename psivalues column to be more descriptive
        final_output_df.rename(columns={'psivalues': 'prediction_psivalues'}, inplace=True)
        
        print(f"\nProcessing complete!")
        print(f"Total records generated: {len(final_output_df)}")
        print(f"Models successfully processed: {len([m for m in all_models_results if not m.empty])}/{len(unique_models)}")
        
        return final_output_df
    else:
        print("No results generated for any models")
        return pd.DataFrame()

# First, let's examine your dataframe structure
print("DataFrame columns:", flattened_df.columns.tolist())
print("\nDataFrame info:")
print(flattened_df.info())
print("\nSample of datefield column:")
print(flattened_df['datefield'].head(10).tolist())

# Check what other date columns might be available
date_columns = ['datefield', 'start_time', 'end_time', 'datereadstartdate']
for col in date_columns:
    if col in flattened_df.columns:
        print(f"\nSample of {col} column:")
        print(flattened_df[col].head(5).tolist())



DataFrame columns: ['customerId', 'digitalLoanAccountId', 'prediction', 'start_time', 'end_time', 'modelDisplayName', 'modelVersionId', 'source', 'datefield', 'train_sdate', 'train_edate', 'test_sdate', 'test_edate', 'datereadstartdate', 'app_avg_time_bw_installed_mins_30d', 'app_cnt_absence_tag_30d', 'app_cnt_absence_tag_90d', 'app_cnt_business_ever', 'app_cnt_competitors_30d', 'app_cnt_competitors_90d', 'app_cnt_education_ever', 'app_cnt_finance_30d', 'app_cnt_finance_7d', 'app_cnt_finance_90d', 'app_cnt_music_and_audio_ever', 'app_cnt_payday_90d', 'app_cnt_rated_for_3plus_ever', 'app_cnt_travel_and_local_ever', 'app_first_competitors_install_to_apply_days', 'app_first_payday_install_to_apply_days', 'app_median_time_bw_installed_mins_30d', 'app_vel_finance_30_over_365', 'apps_score', 'beta_de_ln_age_bin', 'beta_de_ln_appln_day_of_week', 'beta_de_ln_brand_bin', 'beta_de_ln_doc_type_rolled', 'beta_de_ln_education_level', 'beta_de_ln_email_primary_domain', 'beta_de_ln_employment_type_ne

In [47]:
flattened_df['modelDisplayName'][flattened_df['ln_appln_submit_datetime'].isnull()==False].value_counts(dropna=False)

modelDisplayName
Cash_beta_trench1_Demo_backscore          296480
Cash_beta_trench2_demo_backscore          111973
Cash_alpha_trench1_demoscore_backscore     62044
Cash_alpha_trench2_demoscore_backscore     39651
Cash_beta_trench3_demoscore_backscore      38281
Cash_alpha_trench3_demoscore_backscore     16504
Name: count, dtype: int64

In [ ]:
dd.query("""select ln_appln_submit_datetime from flattened_df where ln_appln_submit_datetime is not null;""").to_df()

In [39]:
# Now run the processing
final_result = calculate_psi_for_all_models(flattened_df)
final_result

Found 32 models to process

Processing model 1/32: Beta - AppsScoreModel
Checking datefield for model Beta - AppsScoreModel:
First few values: []
Data type: object

Processing model 2/32: Beta - DemoScoreModel
Checking datefield for model Beta - DemoScoreModel:
First few values: ['ln_appln_submit_datetime', 'ln_appln_submit_datetime', 'ln_appln_submit_datetime', 'ln_appln_submit_datetime', 'ln_appln_submit_datetime']
Data type: object
Using start_time as date column

Processing model 3/32: Beta - StackScoreModel
Checking datefield for model Beta - StackScoreModel:
First few values: ['ln_appln_submit_datetime', 'ln_appln_submit_datetime', 'ln_appln_submit_datetime', 'ln_appln_submit_datetime', 'ln_appln_submit_datetime']
Data type: object
Using start_time as date column

Processing model 4/32: Alpha - CIC-SIL-Model
Checking datefield for model Alpha - CIC-SIL-Model:
First few values: ['ln_appln_submit_datetime', 'ln_appln_submit_datetime', 'ln_appln_submit_datetime', 'ln_appln_submit_da

Empty DataFrame
Columns: []
Index: []